# Cross-validation

## Import packages

In [1]:
from importlib import reload
import os
import glob
import glob2
import pandas as pd
pd.set_option('display.max_columns', 50)
pd.set_option('display.max_rows', 500)
import numpy as np
import sys
import hpfspec
import hpfspecmatch

DIRNAME: /home/tehan/PycharmProjects/hpfspecmatch
/home/tehan/PycharmProjects/hpfspecmatch/library/20210811_specmatch_nir/FITS


/home/tehan/anaconda3/envs/hpf/lib/python3.7/site-packages/radvel/gp.py:33: ImportWarning: celerite not installed. GP kernals using celerite will not work. Try installing celerite using 'pip install celerite'
  Try installing celerite using 'pip install celerite'", ImportWarning)


## Read in Library

In [2]:
# download library if does not exist
hpfspecmatch.utils.get_library()

Library already exists. Skipping download
Library path is: /home/tehan/PycharmProjects/hpfspecmatch/library/20210811_specmatch_nir


In [3]:
# List of stellar library fits files
library_fitsfiles = hpfspecmatch.config.LIBRARY_FITSFILES

# Read in all files as a HPFSpecList object
HLS = hpfspec.HPFSpecList(filelist=library_fitsfiles)

Reading from file /home/tehan/anaconda3/envs/hpf/lib/python3.7/site-packages/hpfspec/data/target_files/GJ_393.config
Barycentric shifting
RVabs iteration #1:  8.33333+- 0.00000km/s
RVabs iteration #2:  8.32934+- 0.00000km/s
berv=-25.48519199698786,rv=8.329341157525445
Reading from file /home/tehan/anaconda3/envs/hpf/lib/python3.7/site-packages/hpfspec/data/target_files/PM_J15118+3933.config
could not convert string to float: 'None' File does not exist!
Querying SIMBAD for data
Saving to file /home/tehan/anaconda3/envs/hpf/lib/python3.7/site-packages/hpfspec/data/target_files/PM_J15118+3933.config
ra 227.9644383333333
dec 39.55058777777778
pmra 96.187
pmdec -154.277
px 33.2582
rv None
epoch 2451545.0
Done
Barycentric shifting
RVabs iteration #1: -15.50000+- 0.00000km/s
RVabs iteration #2: -15.55166+- 0.00000km/s
berv=-10.608760365680746,rv=-15.5516591737958
Reading from file /home/tehan/anaconda3/envs/hpf/lib/python3.7/site-packages/hpfspec/data/target_files/GJ_699.config
Barycentric sh

In [4]:
HLS.splist

[HPFSpec(GJ_393,sn18=475.0),
 HPFSpec(PM_J15118+3933,sn18=74.3),
 HPFSpec(GJ_699,sn18=763.7),
 HPFSpec(GJ_908,sn18=593.3),
 HPFSpec(HD_233153,sn18=279.7),
 HPFSpec(GJ_172,sn18=599.4),
 HPFSpec(Teegarden,sn18=340.3),
 HPFSpec(PM_J02555+2652,sn18=147.9),
 HPFSpec(GJ_53.1_B,sn18=66.7),
 HPFSpec(PM_J16139+3346,sn18=213.0),
 HPFSpec(PM_J08526+2818,sn18=228.8),
 HPFSpec(GJ_213,sn18=598.8),
 HPFSpec(GJ_9304,sn18=468.5),
 HPFSpec(GJ_673,sn18=535.9),
 HPFSpec(GJ_507.1,sn18=350.9),
 HPFSpec(LSPM_J1105+4331W,sn18=295.9),
 HPFSpec(GJ_1148,sn18=409.2),
 HPFSpec(GJ_3991,sn18=455.4),
 HPFSpec(GJ_458.2,sn18=418.3),
 HPFSpec(GJ_480,sn18=377.4),
 HPFSpec(GJ_644_C,sn18=116.6),
 HPFSpec(LSPM_J1916+0510,sn18=288.4),
 HPFSpec(PM_J20034+2951,sn18=111.3),
 HPFSpec(PM_J20112+1611,sn18=132.3),
 HPFSpec(GJ_402,sn18=536.2),
 HPFSpec(GJ_3378,sn18=517.1),
 HPFSpec(GJ_905,sn18=507.8),
 HPFSpec(GJ_273,sn18=584.4),
 HPFSpec(HD_260655,sn18=567.2),
 HPFSpec(BD+00_444,sn18=345.0),
 HPFSpec(V*_V2689_Ori,sn18=314.6),
 HPFS

In [5]:
# Read in library 
df_lib = pd.read_csv(hpfspecmatch.config.PATH_LIBRARY_DB)
df_lib

OBJECT     source      Teff   e_Teff  [Fe/H]  e_[Fe/H]  log(g)  \
0             GJ_9066       Mann  3080.000   60.000  -0.160      0.08   5.053   
1            Ross_128       Mann  3192.000   60.000  -0.020      0.08   5.076   
2             GJ_15_B       Mann  3218.000   60.000  -0.300      0.08   5.072   
3            GJ_105_B       Mann  3284.000   60.000  -0.120      0.03   4.941   
4             GJ_1148       Mann  3304.000   61.000   0.070      0.08   4.814   
5              GJ_273       Mann  3317.000   60.000  -0.110      0.08   4.894   
6             GJ_4333       Mann  3324.000   60.000   0.240      0.08   4.792   
7             GJ_4070       Mann  3400.000   61.000  -0.160      0.08   4.814   
8              GJ_109       Mann  3405.000   60.000  -0.100      0.08   4.852   
9            GJ_725_A  Von Braun  3407.000   15.000  -0.490      0.10   4.900   
10           GJ_687_B  Von Braun  3413.000   28.000  -0.090      0.10   4.850   
11             GJ_436  Von Braun  3416.000   53.000   0.040      0.10   4.830   
12             GJ_581  Von Braun  3442.000   54.000  -0.100      0.10   4.970   
13             GJ_251       Mann  3448.000   60.000  -0.020      0.08   4.877   
14              GJ_70       Mann  3458.000   60.000  -0.130      0.08   4.808   
15             GJ_480       Mann  3463.000   60.000   0.260      0.08   4.771   
16             GJ_411  Von Braun  3464.000   15.000  -0.410      0.10   4.860   
17             GJ_694       Mann  3464.000   61.000   0.000      0.08   4.785   
18             GJ_625       Mann  3475.000   60.000  -0.350      0.08   4.897   
19           GJ_250_B       Mann  3481.000   60.000   0.140      0.03   4.760   
20   LSPM_J1105+4331W  Von Braun  3497.000   39.000  -0.400      0.10   4.870   
21             GJ_361       Mann  3500.000   60.000  -0.050      0.08   4.739   
22            GJ_2066       Mann  3500.000   60.000  -0.120      0.08   4.766   
23           GJ_745_A       Mann  3500.000   60.000  -0.330      0.08   4.927   
24             GJ_849       Mann  3530.000   60.000   0.370      0.08   4.777   
25             GJ_806       Mann  3542.000   61.000  -0.150      0.08   4.781   
26             GJ_393       Mann  3548.000   60.000  -0.180      0.08   4.821   
27    LSPM_J1916+0510       Mann  3558.000   60.000   0.100      0.08   4.764   
28            GJ_15_A  Von Braun  3567.000   11.000  -0.360      0.10   4.870   
29             GJ_649  Von Braun  3590.000   45.000  -0.040      0.10   4.750   
30             GJ_701       Mann  3614.000   60.000  -0.220      0.08   4.788   
31             GJ_526  Von Braun  3618.000   31.000  -0.300      0.10   4.780   
32             GJ_382       Mann  3623.000   60.000   0.130      0.08   4.723   
33             GJ_908       Mann  3646.000   60.000  -0.450      0.08   4.830   
34           GJ_507.1       Mann  3650.000   60.000   0.400      0.08   4.661   
35             GJ_686       Mann  3657.000   60.000  -0.250      0.08   4.829   
36             GJ_173       Mann  3671.000   61.000  -0.040      0.08   4.818   
37             GJ_176  Von Braun  3679.000   77.000   0.150      0.10   4.800   
38           LHS_6128       Mann  3681.000   60.000  -0.370      0.08   4.866   
39             GJ_353       Mann  3692.000   60.000  -0.200      0.08   4.736   
40             GJ_809  Von Braun  3692.000   22.000  -0.210      0.10   4.720   
41             GJ_134       Mann  3700.000   61.000   0.530      0.08   4.648   
42             GJ_880  Von Braun  3713.000   11.000   0.060      0.10   4.720   
43             GJ_514       Mann  3727.000   61.000  -0.090      0.08   4.792   
44             GJ_875       Mann  3740.000   61.000   0.020      0.08   4.699   
45             GJ_895       Mann  3764.000   60.000   0.310      0.08   4.742   
46              GJ_96       Mann  3785.000   62.000   0.140      0.08   4.672   
47          HD_260655       Mann  3801.000   60.000  -0.340      0.08   4.859   
48             GJ_205  Von Braun  3801.000    

## Running Cross-validation for Order 17

In [6]:
# suppress plots in ipython notebook
%matplotlib agg

# run crossvalidation for order 17
order = '17'
df_lib_compare = hpfspecmatch.run_crossvalidation_for_orders(order, df_lib, HLS, plot_results = True)

0
##################
Saving results to /home/tehan/PycharmProjects/hpfspecmatch/library/20210811_specmatch_nir/crossval/o17_crossval/plots/
##################
Created folder: /home/tehan/PycharmProjects/hpfspecmatch/library/20210811_specmatch_nir/crossval/o17_crossval/plots/
##################
Running Chi2 loop
##################
First step: Matching target star to all library stars
##################
Optimization terminated successfully.
         Current function value: 1.621828
         Iterations: 2
         Function evaluations: 120
  1/165, Target = GJ_393             Library Star = PM_J15118+3933     chi2 =  1.622
Optimization terminated successfully.
         Current function value: 2.694355
         Iterations: 1
         Function evaluations: 54
  2/165, Target = GJ_393             Library Star = GJ_699             chi2 =  2.694
Optimization terminated successfully.
         Current function value: 1.383454
         Iterations: 1
         Function evaluations: 55
  3/165, Targ

## Plot 1D Performance 

In [7]:
%matplotlib inline
order = '17'

csv_path = '..'+hpfspecmatch.config.PATH_LIBRARY[len(hpfspecmatch.config.DIRNAME):]+'/crossval/o{}_crossval/crossvalidation_resuls_o{}.csv'.format(order,order)
df_crossval = pd.read_csv(csv_path)

savefolder = '..'+hpfspecmatch.config.PATH_LIBRARY[len(hpfspecmatch.config.DIRNAME):]+'/crossval/o{}_crossval'.format(order)
hpfspecmatch.plot_crossvalidation_results_1d(order,df_crossval,savefolder)

FileNotFoundError: [Errno 2] No such file or directory: '../library/20210811_specmatch_nir/crossval/o17_crossval/crossvalidation_resuls_o17.csv'

## Plot 2D Performance

In [ ]:
order = '17'

csv_path = '..'+hpfspecmatch.config.PATH_LIBRARY[len(hpfspecmatch.config.DIRNAME):]+'/crossval/o{}_crossval/crossvalidation_resuls_o{}.csv'.format(order,order)
df_crossval = pd.read_csv(csv_path)

savefolder = '..'+hpfspecmatch.config.PATH_LIBRARY[len(hpfspecmatch.config.DIRNAME):]+'/crossval/o{}_crossval'.format(order)
hpfspecmatch.plot_crossvalidation_results_2d(order,df_crossval,savefolder)

## Cross-validation Errors 
- We should probably save these into a file that we can read in
- Should we add it to the 2D plot ?

In [ ]:
order = '17'
df_crossval = pd.read_csv('../library/20210406_specmatch_nir_library/crossval/o{}_crossval/crossvalidation_resuls_o{}.csv'.format(order,order))

In [ ]:
np.std(df_crossval.d_teff.values)

In [ ]:
np.std(df_crossval.d_feh)

In [ ]:
np.std(df_crossval.d_logg)